In [7]:
%%html
<script>
(function() {
  // Create the toggle button
  const rtlButton = document.createElement("button");
  rtlButton.textContent = "Toggle LTR";
  rtlButton.id = "top-rtl-toggle";
  rtlButton.style.marginLeft = "8px";
  rtlButton.style.padding = "4px 10px";
  rtlButton.style.fontSize = "14px";
  rtlButton.style.cursor = "pointer";

  // State
  var rtlActive = false;

  // Styling function
  var applyStyleToEditor = (editor) => {
    if (!editor) return;
    var direction = getComputedStyle(editor).getPropertyValue('direction')=='rtl' ? 'ltr' : 'rtl';
    var text_align = getComputedStyle(editor).getPropertyValue('text-align')=='right' ? 'left' : 'right';
    editor.style.setProperty('direction', direction, 'important');
    editor.style.setProperty('text-align', text_align, 'important');
  };

  // Toggle logic
  rtlButton.onclick = () => {
    rtlActive = !rtlActive;
    rtlButton.textContent = rtlActive ? "Toggle LTR" : "Toggle RTL";
    document.querySelectorAll('.jp-MarkdownCell .jp-InputArea-editor').forEach(applyStyleToEditor);
    document.querySelectorAll('.jp-RenderedHTMLCommon code, .jp-RenderedHTMLCommon code span').forEach(applyStyleToEditor);
    document.querySelectorAll('jp-RenderedHTMLCommon, .jp-RenderedHTMLCommon *').forEach(applyStyleToEditor);
  };

  // Watch for focus into editing Markdown cells
  // document.addEventListener('focusin', (event) => {
  //   const editor = event.target.closest('.jp-MarkdownCell .jp-InputArea-editor');
  //    if (editor) applyStyleToEditor(editor);
  // });

  // Insert into top toolbar if not already present
  var insertIntoToolbar = () => {
    const toolbar = document.querySelector('.jp-NotebookPanel-toolbar');
    if (toolbar && !document.getElementById("top-rtl-toggle")) {
      toolbar.appendChild(rtlButton);
    } else {
      // Try again in a moment if toolbar isn't ready yet
      setTimeout(insertIntoToolbar, 300);
    }
  };

  insertIntoToolbar();
})();
</script>

# רשימות (`list`) 

### אג'נדה
- הטיפוס רשימה (`list`)
- אינדקסים ברשימות
- פעולות על רשימות
  - אופרטורים
  - פונקציות
  - מתודות
- רשימות מקוננות - רשימה בתוך רשימה.

במודול זה נתחיל להכיר טיפוס חדש בפייתון – רשימה (`list`).  
רשימה היא **מבנה נתונים** שמאפשר לאחסן אוסף של ערכים במקום אחד, לפי סדר מסוים.
אפשר לחשוב על רשימה כמו קופסה עם תאים, שכל תא מחזיק ערך משלו – מספרים, מחרוזות או אפילו רשימות אחרות.

הרשימות יאפשרו לנו לעבוד עם הרבה נתונים ביחד, לחפש, לשנות ולהשתמש בהם בקלות, במקום לשמור כל ערך בנפרד.

### הצגת "בעיית ניו-זילנד" להדגמת שימוש ברשימות

In [31]:
%%html
<iframe width="560" height="315" src="https://www.youtube.com/embed/csNhZTvbkps?si=-BhCWb_B4ib6V9a1" title="YouTube video player" frameborder="0" allow="accelerometer; autoplay; clipboard-write; encrypted-media; gyroscope; picture-in-picture; web-share" referrerpolicy="strict-origin-when-cross-origin" allowfullscreen></iframe>

#### להלן האלגוריתם שהוצג בקטע הוידאו האחרון:

**בעיה:** ניו זילנד (קלט: `start`, `spend_list`)

1. חשב את הסכום של `spend_list` וקרא לתוצאה `total`

2. `money_left = start - total`

3. חלק את `total` באורך של `spend_list`  
   וקרא לתוצאה `average`

4. `weeks_left = money_left / average`

In [1]:
import json
from jupyterquiz import display_quiz
example = \
'''
[{
    "question": "לו היינו רוצים לחשב את מספר הימים אשר נותר לנו לטייל על סמך התקציב הנוכחי,מה היינו צריכים לשנות בפסאודו קוד?",
    "type": "many_choice",
    "answers": [
        {
            "answer": "יש לכתוב את כל התוכנית מחדש על מנת לפתור את הבעיה.",
            "correct": false,
            "feedback": "לא נכון"
        },
        {
            "answer": "להחליף את שורה 4 בשורה: days_left = 7*(money_left / average).",
            "correct": true,
            "feedback": "נכון!"
        },
        {
            "answer": "להחליף את שורה 1 בשורה:חשב את הסכום של spend_list, חלק סכום זה ב-7 וקרא לתוצאה total.",
            "correct": false,
            "feedback": "לא נכון"
        },
        {
            "answer": "להחליף את שורה 1 בשורה: חשב את הסכום של spend_list, הכפל סכום זה ב-7 וקרא לתוצאה total.",
            "correct": false,
            "feedback": "לא נכון"
        }
    ]
}]
'''
myquiz = json.loads(example)
display_quiz(myquiz)

<IPython.core.display.Javascript object>

בסרטון זה פגשנו אלגוריתם שבו אנחנו רוצים לשמור כמה כסף בני הוציא בכל שבוע במהלך הטיול.
אם היינו יודעים מראש שהטיול נמשך למשל 4 שבועות, יכולנו פשוט להגדיר משתנים נפרדים:
spend1, spend2, spend3, spend4.

אבל - מה יקרה אם הטיול יימשך 3 שבועות? או אולי 10? נצטרך לשנות את הקוד כל פעם מחדש, וזה לא נוח ולא גמיש.

בדיוק כאן נכנסות רשימות (lists) לתמונה:
הרשימה מאפשרת לנו לשמור אוסף ערכים באורך משתנה, כך שהקוד יוכל להתאים את עצמו לטיול קצר או ארוך בלי שנצטרך לשכתב אותו.